In [1]:
%%capture
import warnings
warnings.filterwarnings('ignore')

import os
os.environ["CALITP_BQ_MAX_BYTES"] = str(800_000_000_000)
import shared_utils

from calitp_data_analysis.tables import tbls
import calitp_data_analysis.magics

from siuba import *
import pandas as pd
import geopandas as gpd

import datetime as dt

import importlib
from rt_analysis import rt_filter_map_plot
import build_speedmaps_index

from IPython.display import display, Markdown, Latex, HTML, IFrame
import json
import base64

# Parse traffic signals sheet

In [45]:
df = pd.read_excel('./signals_2023-06-12.xlsx')

In [46]:
df.columns = df.columns.str.replace(' ', '_').str.lower()

In [47]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8256 entries, 0 to 8255
Data columns (total 11 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   imms_id          8240 non-null   object 
 1   tms_unit_type    8256 non-null   object 
 2   district         8256 non-null   int64  
 3   county           8256 non-null   object 
 4   route            8256 non-null   int64  
 5   postmile         8255 non-null   float64
 6   longitude        8256 non-null   float64
 7   latitude         8256 non-null   float64
 8   location         8256 non-null   object 
 9   chronic_flag     91 non-null     object 
 10  tms_unit_status  8256 non-null   object 
dtypes: float64(3), int64(2), object(6)
memory usage: 709.6+ KB


In [48]:
gdf = gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.longitude, df.latitude), crs=shared_utils.geography_utils.WGS84)

In [49]:
signal_gdf = gdf

In [34]:
signal_gdf.explore()

# Speedmaps

In [6]:
## parameters cell
itp_id = 300

In [7]:
analysis_date = build_speedmaps_index.ANALYSIS_DATE

In [8]:
%%capture_parameters
human_date = analysis_date.strftime('%B %d %Y (%A)')
human_date

{"human_date": "July 12 2023 (Wednesday)"}


In [9]:
%%capture
rt_day = rt_filter_map_plot.from_gcs(itp_id, analysis_date)

In [10]:
%%capture_parameters
organization_name = rt_day.organization_name
organization_name

{"organization_name": "City of Santa Monica"}


## Morning Peak

In [11]:
%%capture
rt_day.set_filter(start_time='06:00', end_time='09:00')

### 20th Percentile Speeds by Segment

In [12]:
%%capture
_m = rt_day.segment_speed_map(how='low_speeds', no_title=True, shn=True,
                             no_render=True
                            )

In [13]:
%%capture
rt_day.map_gz_export()

In [14]:
rt_day.render_spa_link()

<a href="https://embeddable-maps.calitp.org/?state=eyJuYW1lIjogIm51bGwiLCAibGF5ZXJzIjogW3sibmFtZSI6ICJEMDcgU3RhdGUgSGlnaHdheSBOZXR3b3JrIiwgInVybCI6ICJodHRwczovL3N0b3JhZ2UuZ29vZ2xlYXBpcy5jb20vY2FsaXRwLW1hcC10aWxlcy9zcGVlZHNfMjAyMy0wNy0xMi8wN19TSE4uZ2VvanNvbi5neiIsICJwcm9wZXJ0aWVzIjogeyJzdHJva2VkIjogZmFsc2UsICJoaWdobGlnaHRfc2F0dXJhdGlvbl9tdWx0aXBsaWVyIjogMC41fSwgInR5cGUiOiAic3RhdGVfaGlnaHdheV9uZXR3b3JrIn0sIHsibmFtZSI6ICJDaXR5IG9mIFNhbnRhIE1vbmljYSBKdWwgMTIsIDIwMjMgKFdlZCkgQU0gUGVhayIsICJ1cmwiOiAiaHR0cHM6Ly9zdG9yYWdlLmdvb2dsZWFwaXMuY29tL2NhbGl0cC1tYXAtdGlsZXMvc3BlZWRzXzIwMjMtMDctMTIvMzAwX0FNX1BlYWtfc3BlZWRzLmdlb2pzb24uZ3oiLCAicHJvcGVydGllcyI6IHsic3Ryb2tlZCI6IGZhbHNlLCAiaGlnaGxpZ2h0X3NhdHVyYXRpb25fbXVsdGlwbGllciI6IDAuNSwgInRvb2x0aXBfc3BlZWRfa2V5IjogInAyMF9tcGgifSwgInR5cGUiOiAic3BlZWRtYXAifV0sICJsYXRfbG9uIjogWzM0LjAyNzc1OTM4NTYyMTEsIC0xMTguNDQ3NTI3NTc4NDU3MzRdLCAiem9vbSI6IDEzLCAibGVnZW5kX3VybCI6ICJodHRwczovL3N0b3JhZ2UuZ29vZ2xlYXBpcy5jb20vY2FsaXRwLW1hcC10aWxlcy9zcGVlZHNfbGVnZW5kLnN2ZyJ9" target="_blank">Open Full Map in New Tab</a>

In [15]:
rt_day.display_spa_map()

## Add Signals

In [16]:
from shared_utils import rt_utils

In [17]:
rt_utils.set_state_export?

Signature:
rt_utils.set_state_export(
    gdf,
    bucket: str = 'calitp-map-tiles/',
    subfolder: str = 'testing/',
    filename: str = 'test2',
    map_type: Literal['speedmap', 'speed_variation', 'hqta_areas', 'hqta_stops', 'state_highway_network'] = None,
    map_title: str = 'Map',
    cmap: branca.colormap.ColorMap = None,
    color_col: str = None,
    legend_url: str = None,
    existing_state: dict = {},
    cache_seconds: int = 3600,
)
Docstring:
Applies light formatting to gdf for successful spa display. Will pass map_type
if supported by the spa and provided. GCS bucket is preset to the publically
available one.
Supply cmap and color_col for coloring based on a Branca ColorMap and a column
to apply the color to.
Cache is 1 hour by default, can set shorter time in seconds for
"near realtime" applications (suggest 120) or development (suggest 0)

Returns dict with state dictionary and map URL. Can call multiple times and supply
previous state as existing_state to create mul

In [18]:
rt_utils.set_state_export(gdf, filename='signals_all', existing_state=rt_day.spa_map_state)

writing to calitp-map-tiles/testing/signals_all.geojson.gz


{'state_dict': {'name': 'null',
  'layers': [{'name': 'D07 State Highway Network',
    'url': 'https://storage.googleapis.com/calitp-map-tiles/speeds_2023-07-12/07_SHN.geojson.gz',
    'properties': {'stroked': False, 'highlight_saturation_multiplier': 0.5},
    'type': 'state_highway_network'},
   {'name': 'City of Santa Monica Jul 12, 2023 (Wed) AM Peak',
    'url': 'https://storage.googleapis.com/calitp-map-tiles/speeds_2023-07-12/300_AM_Peak_speeds.geojson.gz',
    'properties': {'stroked': False,
     'highlight_saturation_multiplier': 0.5,
     'tooltip_speed_key': 'p20_mph'},
    'type': 'speedmap'},
   {'name': 'Map',
    'url': 'https://storage.googleapis.com/calitp-map-tiles/testing/signals_all.geojson.gz',
    'properties': {'stroked': False, 'highlight_saturation_multiplier': 0.5}}],
  'lat_lon': (35.85061665299428, -119.74721098078534),
  'zoom': 13,
  'legend_url': 'https://storage.googleapis.com/calitp-map-tiles/speeds_legend.svg'},
 'spa_link': 'https://embeddable-maps.

## Segment Matching Algo

In [50]:
district = int(rt_day.caltrans_district[:2])

In [67]:
dist_signals = (signal_gdf >> filter(_.district == district)
                   >> filter(_.tms_unit_type != 'Freeway Ramp Meters')
                   >> select(_.imms_id, _.location, _.geometry)
               ).copy()

In [68]:
dist_signals >> head(3)

imms_id             location                     geometry
3876  07LA001 -ED020       STUDEBAKER RD.  POINT (-118.10716 33.75381)
3877  07LA001 -ED021  2ND ST-WESTMINISTER  POINT (-118.11114 33.75812)
3878  07LA001 -ED022      MARINA PACIFICA  POINT (-118.11337 33.76049)

In [77]:
dist_signals_points = dist_signals.to_crs(shared_utils.geography_utils.CA_NAD83Albers)
dist_signals_buffered = dist_signals_points.copy()
dist_signals_buffered.geometry = dist_signals_buffered.buffer(400)

In [78]:
# buffer 400 and sjoin, then filter by signal...

In [79]:
rt_day.detailed_map_view >> head(3)

stop_id                 stop_name  \
597    None                      None   
598    1314  CRENSHAW SB & OLYMPIC FS   
599    1315     PICO WB & CRENSHAW FS   

                                              geometry shape_id  \
597  POLYGON ((-118.30932 34.06209, -118.30895 34.0...    26410   
598  POLYGON ((-118.32324 34.05454, -118.32345 34.0...    26410   
599  POLYGON ((-118.32680 34.04806, -118.32701 34.0...    26410   

     stop_sequence route_id route_short_name  direction_id  p50_mph  p20_mph  \
597            1.5     3621               R7           1.0     27.2     27.2   
598            3.0     3621               R7           1.0     11.6     11.6   
599            4.0     3621               R7           1.0     12.8     12.8   

     p80_mph  fast_slow_ratio  trips_per_hour  miles_from_last time_formatted  
597     27.2              1.0             0.3              1.2           2:38  
598     11.6              1.0             0.3              0.5           2:35  
599     12.8              1.0             0.3              0.5           2:20

In [80]:
dmv_proj = rt_day.detailed_map_view.to_crs(shared_utils.geography_utils.CA_NAD83Albers)

In [85]:
joined = gpd.sjoin(dmv_proj, dist_signals_buffered) >> select(-_.index_right)

In [86]:
joined >> head(3)

stop_id                                   stop_name  \
610     621  PICO WB & SEPULVEDA NS (Sepulveda Station)   
611      76                          PICO WB & BUNDY NS   
309     257                    OLYMPIC WB & SAWTELLE NS   

                                              geometry shape_id  \
610  POLYGON ((145086.514 -440472.578, 145079.551 -...    26410   
611  POLYGON ((144070.938 -441119.758, 143888.176 -...    26410   
309  POLYGON ((144214.162 -440475.275, 144209.921 -...    26358   

     stop_sequence route_id route_short_name  direction_id  p50_mph  p20_mph  \
610           14.0     3621               R7           1.0     11.0     11.0   
611           15.0     3621               R7           1.0     15.5     15.5   
309           24.0     3608                5           1.0      7.0      7.0   

     p80_mph  fast_slow_ratio  trips_per_hour  miles_from_last time_formatted  \
610     11.0              1.0             0.3              0.4           2:10   
611     15.5              1.0             0.3              1.0           3:52   
309      7.0              1.0             0.7              0.2           1:42   

            imms_id                         location  
610  07LA405 -ED543  SAWTELLE BLVD. -TENNESSE AVENUE  
611  07LA405 -ED543  SAWTELLE BLVD. -TENNESSE AVENUE  
309  07LA405 -ED543  SAWTELLE BLVD. -TENNESSE AVENUE

In [89]:
##TODO filter by approach direction for directional signals (noted as start of this string...)
# list(dist_signals.location.str[:3])

Re-add point geom, find approaching segments...

In [90]:
dist_signals_points >> head(3)

imms_id             location                        geometry
3876  07LA001 -ED020       STUDEBAKER RD.  POINT (175403.296 -471720.410)
3877  07LA001 -ED021  2ND ST-WESTMINISTER  POINT (175024.972 -471250.016)
3878  07LA001 -ED022      MARINA PACIFICA  POINT (174813.381 -470990.814)

In [111]:
points_for_join = dist_signals_points >> select(_.imms_id, _.signal_pt_geom == _.geometry)

In [112]:
joined_signal_points = joined >> inner_join(_, points_for_join, on ='imms_id')

In [113]:
seg_lines = (rt_day.stop_segment_speed_view.copy()
                >> select(_.line_geom == _.geometry, _.shape_id, _.stop_sequence)
                >> distinct(_.line_geom, _.shape_id, _.stop_sequence)
            )

In [114]:
joined_seg_lines = joined_signal_points >> inner_join(_, seg_lines, on = ['shape_id', 'stop_sequence'])

In [115]:
segment = joined_seg_lines.line_geom.iloc[0]

In [116]:
import shapely

In [124]:
def segment_signal_distance(row):
    segment = row.line_geom
    start = shapely.ops.substring(segment, 0, 0)
    end = shapely.ops.substring(segment, segment.length, segment.length)
    one_signal = row.signal_pt_geom
    row['start_distance'] = start.distance(one_signal)
    row['end_distance'] = end.distance(one_signal)
    
    return row

In [126]:
joined_seg_lines = joined_seg_lines.apply(segment_signal_distance, axis = 1)
joined_seg_lines['approaching'] = joined_seg_lines.end_distance < joined_seg_lines.start_distance

In [127]:
joined_seg_lines.approaching.value_counts()

True     535
False    526
Name: approaching, dtype: int64

In [129]:
joined_seg_lines.columns

Index(['stop_id', 'stop_name', 'geometry', 'shape_id', 'stop_sequence',
       'route_id', 'route_short_name', 'direction_id', 'p50_mph', 'p20_mph',
       'p80_mph', 'fast_slow_ratio', 'trips_per_hour', 'miles_from_last',
       'time_formatted', 'imms_id', 'location', 'signal_pt_geom', 'line_geom',
       'start_distance', 'end_distance', 'approaching'],
      dtype='object')

In [130]:
gdf = (joined_seg_lines
          >> filter(_.approaching)
          >> select(-_.signal_pt_geom, -_.line_geom)
      )

In [131]:
rt_utils.set_state_export(gdf, filename='signal_join_test', cache_seconds=0)

writing to calitp-map-tiles/testing/signal_join_test.geojson.gz


{'state_dict': {'name': 'null',
  'layers': [{'name': 'Map',
    'url': 'https://storage.googleapis.com/calitp-map-tiles/testing/signal_join_test.geojson.gz',
    'properties': {'stroked': False, 'highlight_saturation_multiplier': 0.5}}],
  'lat_lon': (34.01857777827609, -118.42706343267064),
  'zoom': 13},
 'spa_link': 'https://embeddable-maps.calitp.org/?state=eyJuYW1lIjogIm51bGwiLCAibGF5ZXJzIjogW3sibmFtZSI6ICJNYXAiLCAidXJsIjogImh0dHBzOi8vc3RvcmFnZS5nb29nbGVhcGlzLmNvbS9jYWxpdHAtbWFwLXRpbGVzL3Rlc3Rpbmcvc2lnbmFsX2pvaW5fdGVzdC5nZW9qc29uLmd6IiwgInByb3BlcnRpZXMiOiB7InN0cm9rZWQiOiBmYWxzZSwgImhpZ2hsaWdodF9zYXR1cmF0aW9uX211bHRpcGxpZXIiOiAwLjV9fV0sICJsYXRfbG9uIjogWzM0LjAxODU3Nzc3ODI3NjA5LCAtMTE4LjQyNzA2MzQzMjY3MDY0XSwgInpvb20iOiAxM30='}

### Variation in Speeds by Segment

* This visualization shows variation as the ratio between the 80th percentile and 20th percentile speeds in each segment
* Segments with high variation in speeds make it difficult for transit operators to set accurate schedules, and can cause inconsistent service for riders

In [ ]:
rt_day.map_variance(no_render=True)

In [ ]:
%%capture
rt_day.map_gz_export(map_type = 'variance')

In [ ]:
rt_day.render_spa_link()

In [ ]:
rt_day.display_spa_map()